Notebook to test some ideas for plotting the waddington landscape from our sequencing data.
For now I will explore which single cell metrics from the scRNAseq work best to define the landscape topology.

<!-- Consider however, that in the future we might want to compute some kind of state centroid so that we can project some of the data from the cytof side (ie response of the different states to external cues as determined by Fig5 D) -->

<!-- **Early December update**
Make a WT and an AK landscape. 
For the slides, we would need to create static images of the 2 landscapes from 
the same angle. Additionally we would need to create an image of all INT epi on a SCENT landscape from the same angle -->


In [1]:
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import graphtools
from scipy.interpolate import Rbf
from sklearn.preprocessing import MinMaxScaler

#This grid sets both range of phate dims and the number of "ticks" -> controls "resolution"
grid_x, grid_y = np.mgrid[-0.035:0.045:0.0024, -0.025:0.045:0.0024]

In [2]:
import plotly.io as pio

# This ensures Plotly output works in multiple places:
# plotly_mimetype: VS Code notebook UI
# notebook: "Jupyter: Export to HTML" command in VS Code
# See https://plotly.com/python/renderers/#multiple-renderers
pio.renderers.default = "plotly_mimetype+notebook"

In [3]:
#Functions

def compute_distdeg(input_df, split_by="curatedCLUST", 
    col_list=["phateepi_1","phateepi_2"], 
    knn=30, distance_metric = "manhattan", scale = True, inv_degree=True,
    plot=False, rmv_outliers=True):
    #Function that computes distances and degrees of cells within a cluster
    #Results will get scaled within the cluster level so it handles them as independent entities
    output_df = pd.DataFrame(columns=col_list+["dist","deg"])
    for i in input_df[split_by].unique():
        print(i)
        df_dist = input_df.loc[input_df[split_by]==i,col_list]
        #Knn param is key and must be tunned according to the size of the cluster
        G = graphtools.Graph(df_dist.values, knn=knn, decay=None, distance=distance_metric)
        # Return distances by using shortest_path
        np_dist = G.shortest_path(distance="data")
        #Compute median distance to all cells for al cells -> min should be a centroid
        df_dist["dist"] = np.median(np_dist, axis=1)
        df_dist["deg"] = G.to_pygsp().d
        if rmv_outliers:
            #Replace distant outliers with median value -> DONE to smoothen landscape at the very edges of a cluster
            df_dist["dist"] = np.where(
                                df_dist["dist"]>np.percentile(df_dist["dist"],99), 
                                df_dist["dist"].median(), 
                                df_dist["dist"])
        if scale:
            df_dist["dist_scaled"] = MinMaxScaler().fit_transform(X = df_dist[["dist"]])
            df_dist["inv_deg_scaled"] = MinMaxScaler().fit_transform(X = 1/df_dist[["deg"]])
        if plot:
            #Plot cluster cells on phate and colour by distance from centroid
            plt.scatter(df_dist["phateepi_1"],df_dist["phateepi_2"],c=df_dist["dist"])
            plt.show()
            plt.scatter(df_dist["phateepi_1"],df_dist["phateepi_2"],c=df_dist["deg"])
            plt.show()

        output_df = pd.concat([output_df, df_dist])

    return output_df


# Load and process data

Compute centroids of the clusters and compute a distance for all belonging cells.

In [4]:
cell_data = pd.read_csv("input/md_scRNAseq.csv").iloc[:,:13]

empty_df = compute_distdeg(cell_data, knn=50, plot=False)

#Add distances and degrees to main dataframe
cell_data = pd.merge(cell_data, empty_df.sort_index(), how="left",on=["phateepi_1","phateepi_2"])
del empty_df

#Scale velocity length for all cells
cell_data["inv_velo_scaled"] = MinMaxScaler().fit_transform(X = 1/cell_data[["velocity_length"]])

cell_data

TA 1
Goblet / DCS
Late Enterocyte
proCSC
Early Enterocyte
revCSC
ER Stress
CSC
TA 2


phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR   
0       -0.003110   -0.003080    0.274730       186.242097  0  0  0     0  \
1        0.024983    0.029213    0.233824       152.058837  0  0  0     0   
2        0.037142    0.007396    0.195300       164.789267  0  0  0     0   
3       -0.021990    0.000884    0.359556       221.681973  0  0  0     0   
4        0.041909    0.035762    0.230588       208.885837  0  0  0     0   
...           ...         ...         ...              ... .. .. ..   ...   
29249   -0.003300   -0.006133    0.361533       197.806256  0  0  0     1   
29250   -0.028562    0.010894    0.443155       145.233683  0  0  0     1   
29251   -0.002911   -0.009425    0.392001       188.500721  0  0  0     1   
29252   -0.024535    0.002836    0.441813       114.664223  0  0  0     1   
29253   -0.013252    0.004670    0.434362       191.966684  0  0  0     1   

       mac  fib     curatedCLUST  OWNsig_stemO_UCell  OWNsig_stemS_UCell   
0        0    0             TA 1            0.000000            0.221648  \
1        0    0     Goblet / DCS            0.000000            0.122389   
2        0    0  Late Enterocyte            0.000000            0.155778   
3        0    0           proCSC            0.013370            0.085037   
4        0    0  Late Enterocyte            0.000000            0.058852   
...    ...  ...              ...                 ...                 ...   
29249    0    0             TA 1            0.179889            0.337778   
29250    0    0           proCSC            0.663185            0.256611   
29251    0    0              CSC            0.136074            0.283296   
29252    0    0           proCSC            0.298593            0.203278   
29253    0    0           revCSC            0.512222            0.388148   

           dist deg  dist_scaled  inv_deg_scaled  inv_velo_scaled  
0      0.005812  62     0.125762        0.544900         0.147660  
1      0.017262  51     0.145049        0.949755         0.231605  
2      0.015681  73     0.193456        0.259163         0.196273  
3      0.007606  53     0.129802        0.868918         0.087964  
4      0.041542  50     0.936662        1.000000         0.107182  
...         ...  ..          ...             ...              ...  
29249  0.004747  55     0.001310        0.786241         0.125830  
29250  0.007139  50     0.103965        1.000000         0.253098  
29251  0.006407  53     0.091558        0.854953         0.143186  
29252  0.006489  51     0.068031        0.954592         0.380759  
29253  0.010792  51     0.620195        0.948767         0.136525  

[29254 rows x 18 columns]

In [5]:
colours = {
    "TA 1":"#FF99CC",
    "Goblet / DCS":"#CC9900",
    "Late Enterocyte":"#006600",
    "proCSC":"#000099",
    "Early Enterocyte":"#00FF99",
    "revCSC":"#CC0000",
    "ER Stress":"#CC00FF",
    "CSC":"#6666FF",
    "TA 2":"#FF6666"
    }

fig = go.Figure(data=[go.Scatter3d(
        x=cell_data["phateepi_1"], 
        y=cell_data["phateepi_2"], 
        z=cell_data["SCENT_ccat"],
        mode="markers", marker=dict(
            color=cell_data["curatedCLUST"].map(colours)))])
fig.update_traces(marker_size = 2)
fig.update_layout(
    autosize=True,
    scene_aspectmode="cube",
    width=1000, height=1000,
    margin=dict(l=50, r=50, b=50, t=90))
fig.show()

# Generate landscapes for each condition

WT monoculture

In [6]:
wt_data = cell_data.loc[(~cell_data["velocity_length"].isna()) & (cell_data["WENR"]==0) & (cell_data["fib"]==0)]
wt_data = wt_data.loc[wt_data["A"]==0]
wt_data

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR   
0       -0.003110   -0.003080    0.274730       186.242097  0  0  0     0  \
1        0.024983    0.029213    0.233824       152.058837  0  0  0     0   
2        0.037142    0.007396    0.195300       164.789267  0  0  0     0   
3       -0.021990    0.000884    0.359556       221.681973  0  0  0     0   
4        0.041909    0.035762    0.230588       208.885837  0  0  0     0   
...           ...         ...         ...              ... .. .. ..   ...   
27858   -0.012149   -0.011766    0.363156       257.277901  0  0  0     0   
27859    0.033928    0.000319    0.234797       163.557290  0  0  0     0   
27860    0.024310    0.027719    0.236899       193.132956  0  0  0     0   
27861   -0.006890    0.000370    0.366593       264.817601  0  0  0     0   
27862   -0.001739   -0.010089    0.305169       231.291395  0  0  0     0   

       mac  fib     curatedCLUST  OWNsig_stemO_UCell  OWNsig_stemS_UCell   
0        0    0             TA 1             0.00000            0.221648  \
1        0    0     Goblet / DCS             0.00000            0.122389   
2        0    0  Late Enterocyte             0.00000            0.155778   
3        0    0           proCSC             0.01337            0.085037   
4        0    0  Late Enterocyte             0.00000            0.058852   
...    ...  ...              ...                 ...                 ...   
27858    0    0              CSC             0.00000            0.229426   
27859    0    0  Late Enterocyte             0.00000            0.066667   
27860    0    0     Goblet / DCS             0.00000            0.132981   
27861    0    0             TA 1             0.00000            0.277037   
27862    0    0             TA 1             0.00000            0.140685   

           dist deg  dist_scaled  inv_deg_scaled  inv_velo_scaled  
0      0.005812  62     0.125762        0.544900         0.147660  
1      0.017262  51     0.145049        0.949755         0.231605  
2      0.015681  73     0.193456        0.259163         0.196273  
3      0.007606  53     0.129802        0.868918         0.087964  
4      0.041542  50     0.936662        1.000000         0.107182  
...         ...  ..          ...             ...              ...  
27858  0.007551  50     0.201416        1.000000         0.044559  
27859  0.011185  60     0.064243        0.608108         0.199451  
27860  0.015684  60     0.083408        0.572917         0.134337  
27861  0.008397  56     0.427906        0.748069         0.036863  
27862  0.006038  60     0.152231        0.608108         0.074930  

[1511 rows x 18 columns]

WT + fibroblast co-culture

In [7]:
wtfib_data = cell_data.loc[(~cell_data["velocity_length"].isna()) & (cell_data["WENR"]==0) & (cell_data["fib"]==1)]
wtfib_data = wtfib_data.loc[wtfib_data["A"]==0]
wtfib_data

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR  mac   
6633    0.028569    0.002332    0.211259        80.530242  0  0  0     0    0  \
6634    0.002677   -0.007119    0.301441       276.028593  0  0  0     0    0   
6635   -0.006586    0.001626    0.339790       282.541646  0  0  0     0    0   
6636   -0.004062    0.011612    0.313816       191.022168  0  0  0     0    0   
6637   -0.020976    0.000697    0.395898       193.642173  0  0  0     0    0   
...          ...         ...         ...              ... .. .. ..   ...  ...   
7767    0.035519    0.005709    0.295729       244.941703  0  0  0     0    0   
7768    0.013063   -0.013518    0.319500       263.922364  0  0  0     0    0   
7769    0.003459    0.021346    0.279131        91.355214  0  0  0     0    0   
7770    0.027127   -0.001343    0.259780       207.349972  0  0  0     0    0   
7771   -0.001538   -0.005911    0.350759       282.467727  0  0  0     0    0   

      fib      curatedCLUST  OWNsig_stemO_UCell  OWNsig_stemS_UCell      dist   
6633    1   Late Enterocyte            0.006074            0.230463  0.009271  \
6634    1              TA 1            0.000000            0.506056  0.006843   
6635    1            revCSC            0.013667            0.463593  0.006825   
6636    1            revCSC            0.000000            0.562259  0.007560   
6637    1            proCSC            0.397778            0.383222  0.007949   
...   ...               ...                 ...                 ...       ...   
7767    1  Early Enterocyte            0.000000            0.127630  0.031458   
7768    1  Early Enterocyte            0.000000            0.281185  0.007886   
7769    1         ER Stress            0.000000            0.242185  0.009613   
7770    1   Late Enterocyte            0.000000            0.382167  0.009231   
7771    1              TA 1            0.000000            0.609185  0.004902   

     deg  dist_scaled  inv_deg_scaled  inv_velo_scaled  
6633  70     0.009226        0.328185         0.637838  
6634  55     0.246332        0.786241         0.026197  
6635  54     0.209827        0.806452         0.020389  
6636  57     0.285858        0.679117         0.138316  
6637  57     0.148760        0.715605         0.133390  
...   ..          ...             ...              ...  
7767  50     0.780503        1.000000         0.058173  
7768  71     0.040550        0.304530         0.037754  
7769  51     0.270472        0.948767         0.535508  
7770  58     0.008065        0.675676         0.109648  
7771  54     0.019354        0.825826         0.020454  

[1139 rows x 18 columns]

WENR

In [8]:
wenr_data = cell_data.loc[(~cell_data["velocity_length"].isna()) & (cell_data["WENR"]==1)]
wenr_data

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR   
27863   -0.018816   -0.003791    0.415167       161.200107  0  0  0     1  \
27864   -0.026489    0.007999    0.437117       134.310152  0  0  0     1   
27865   -0.009203   -0.001552    0.391960       193.822863  0  0  0     1   
27866   -0.018275    0.001083    0.445214       132.371841  0  0  0     1   
27867    0.021535   -0.009514    0.321326       257.039718  0  0  0     1   
...           ...         ...         ...              ... .. .. ..   ...   
29249   -0.003300   -0.006133    0.361533       197.806256  0  0  0     1   
29250   -0.028562    0.010894    0.443155       145.233683  0  0  0     1   
29251   -0.002911   -0.009425    0.392001       188.500721  0  0  0     1   
29252   -0.024535    0.002836    0.441813       114.664223  0  0  0     1   
29253   -0.013252    0.004670    0.434362       191.966684  0  0  0     1   

       mac  fib      curatedCLUST  OWNsig_stemO_UCell  OWNsig_stemS_UCell   
27863    0    0               CSC            0.662370            0.241815  \
27864    0    0            proCSC            0.568963            0.245481   
27865    0    0              TA 2            0.408926            0.391481   
27866    0    0            proCSC            0.354852            0.361333   
27867    0    0  Early Enterocyte            0.026185            0.200870   
...    ...  ...               ...                 ...                 ...   
29249    0    0              TA 1            0.179889            0.337778   
29250    0    0            proCSC            0.663185            0.256611   
29251    0    0               CSC            0.136074            0.283296   
29252    0    0            proCSC            0.298593            0.203278   
29253    0    0            revCSC            0.512222            0.388148   

           dist deg  dist_scaled  inv_deg_scaled  inv_velo_scaled  
27863  0.014193  67     0.839500        0.349813         0.205669  
27864  0.005365  54     0.005803        0.828460         0.292043  
27865  0.004556  68     0.007054        0.434492         0.133056  
27866  0.009080  59     0.211367        0.646744         0.299625  
27867  0.012076  60     0.172074        0.608108         0.044810  
...         ...  ..          ...             ...              ...  
29249  0.004747  55     0.001310        0.786241         0.125830  
29250  0.007139  50     0.103965        1.000000         0.253098  
29251  0.006407  53     0.091558        0.854953         0.143186  
29252  0.006489  51     0.068031        0.954592         0.380759  
29253  0.010792  51     0.620195        0.948767         0.136525  

[1391 rows x 18 columns]

AK monoculture

In [9]:
ak_data = cell_data.loc[(~cell_data["velocity_length"].isna()) & (cell_data["WENR"]==0) & (cell_data["fib"]==0)]
ak_data = ak_data.loc[ak_data["A"]==1]
ak_data

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR  mac   
2480    0.003240    0.016035    0.412615       103.453230  1  1  0     0    0  \
2481   -0.016968   -0.007710    0.391436        77.548857  1  1  0     0    0   
2482    0.006557    0.004918    0.363780       110.565845  1  1  0     0    0   
2483   -0.006996   -0.007648    0.335951        78.394814  1  1  0     0    0   
2484   -0.028062    0.014227    0.399498        60.276537  1  1  0     0    0   
...          ...         ...         ...              ... .. .. ..   ...  ...   
4335   -0.008400   -0.004858    0.401780        70.411602  1  1  0     0    0   
4336    0.009121   -0.014316    0.359641        86.534077  1  1  0     0    0   
4337   -0.017137   -0.003249    0.408179       114.401401  1  1  0     0    0   
4338   -0.010983   -0.004122    0.423684       100.011907  1  1  0     0    0   
4339   -0.025789    0.007222    0.425584        75.027410  1  1  0     0    0   

      fib      curatedCLUST  OWNsig_stemO_UCell  OWNsig_stemS_UCell      dist   
2480    0         ER Stress            0.307222            0.167796  0.006067  \
2481    0            proCSC            0.312296            0.092093  0.015171   
2482    0         ER Stress            0.329222            0.146759  0.009984   
2483    0              TA 1            0.020519            0.058222  0.005786   
2484    0            proCSC            0.385741            0.124241  0.009885   
...   ...               ...                 ...                 ...       ...   
4335    0              TA 1            0.411444            0.089111  0.006204   
4336    0  Early Enterocyte            0.038741            0.084074  0.008323   
4337    0            proCSC            0.284037            0.105444  0.011822   
4338    0              TA 2            0.575481            0.089889  0.005247   
4339    0            proCSC            0.369815            0.180352  0.005551   

     deg  dist_scaled  inv_deg_scaled  inv_velo_scaled  
2480  65     0.016260        0.397022         0.446485  
2481  65     0.548308        0.465587         0.671038  
2482  57     0.297065        0.679117         0.403241  
2483  59     0.122754        0.641319         0.661361  
2484  68     0.255870        0.386997         0.928015  
...   ..          ...             ...              ...  
4335  60     0.171561        0.608108         0.761941  
4336  56     0.054286        0.748069         0.577921  
4337  64     0.363017        0.493421         0.382152  
4338  68     0.050685        0.434492         0.469616  
4339  50     0.016127        1.000000         0.701177  

[1860 rows x 18 columns]

Group landscapes together in a dict

In [10]:
df_dict = {"WT":wt_data, "WtFib":wtfib_data, "WENR":wenr_data,"AK":ak_data}

for key, df in df_dict.items():
    df["CCATmed"] = df.groupby(by="curatedCLUST")[["SCENT_ccat"]].transform("median")
    df["invVELOmed"]= df.groupby(by="curatedCLUST")[["inv_velo_scaled"]].transform("median")


/tmp/ipykernel_32308/521725036.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_32308/521725036.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Plot the landscapes

Compute VR score, interpolate to a landscape, and plot results.

In [11]:
for key,df in df_dict.items():
    df_2 = df.copy()
    df_2["VR"] = df_2.apply(
        lambda x: 0.9*x["CCATmed"]+0.1*(x["invVELOmed"]*x["dist_scaled"]), 
        axis=1)

    rbfi = Rbf(df_2["phateepi_1"], df_2["phateepi_2"], 
                df_2["VR"], 
                smooth=1, kernel = "thin_plate_spline")
    di = rbfi(grid_x, grid_y)
    
    # Change all values on interpolated grid that go above the max height in data
    di[di>(round(df_2["VR"].max(),2)+0.02)] = None



    fig = go.Figure(data=[go.Surface(x=grid_x,y=grid_y,z=di)])
    fig.update_traces(colorscale=[[0,"blue"],[0.25,"green"],[0.5,"yellow"],[0.75,"#5f3316"],[0.85,"#513b1b"],[1,"white"]],cmax=0.38, cmin=0.22)
    fig.add_scatter3d(
        x=df_2.dropna()["phateepi_1"],
        y=df_2.dropna()["phateepi_2"], 
        z=((0.1*df_2.dropna()["SCENT_ccat"]+0.9*df_2.dropna()["VR"])+0.012),
        mode="markers",
        marker=dict(
            size=4, 
            color=df_2.dropna()["curatedCLUST"].map(colours),
            opacity=0.42,
            # line=dict(width=2,
            #     color="darkgrey")
            )
        )
    fig.update_layout(
        title=None,
        template = "simple_white",
        scene = dict(
            xaxis = dict(nticks=5,title=""),
            yaxis = dict(nticks=5, title = ""),
            zaxis = dict(nticks=5, range=[0.2,0.45], title="")),
        autosize=True,
        width=1000, height=1000,
        margin=dict(l=0, r=0, b=0, t=0),
        scene_aspectmode="cube",
        scene_camera=dict(
            up=dict(x=0, y=0, z=1),
            center=dict(x=0, y=0, z=0),
            eye=dict(x=1.5, y=1, z=2)
        )
        )
    fig.show()
    fig.write_html(f"output/plot_{key}_LANDSCAPE.html")
    fig.write_image(f"output/plot_{key}_LANDSCAPE.pdf", scale=2)

# Generate and export landscape dataframes

In [12]:
landscape_dict = {}
for key,df in df_dict.items():
    df_landscape = df.copy()
    df_landscape["VR"] = df_landscape.apply(
        lambda x: 0.9*x["CCATmed"]+0.1*(x["invVELOmed"]*x["dist_scaled"]),
        axis=1)
    landscape_dict[key] = df_landscape

In [13]:
landscape_dict["WT"]

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR   
0       -0.003110   -0.003080    0.274730       186.242097  0  0  0     0  \
1        0.024983    0.029213    0.233824       152.058837  0  0  0     0   
2        0.037142    0.007396    0.195300       164.789267  0  0  0     0   
3       -0.021990    0.000884    0.359556       221.681973  0  0  0     0   
4        0.041909    0.035762    0.230588       208.885837  0  0  0     0   
...           ...         ...         ...              ... .. .. ..   ...   
27858   -0.012149   -0.011766    0.363156       257.277901  0  0  0     0   
27859    0.033928    0.000319    0.234797       163.557290  0  0  0     0   
27860    0.024310    0.027719    0.236899       193.132956  0  0  0     0   
27861   -0.006890    0.000370    0.366593       264.817601  0  0  0     0   
27862   -0.001739   -0.010089    0.305169       231.291395  0  0  0     0   

       mac  fib  ... OWNsig_stemO_UCell  OWNsig_stemS_UCell      dist  deg   
0        0    0  ...            0.00000            0.221648  0.005812   62  \
1        0    0  ...            0.00000            0.122389  0.017262   51   
2        0    0  ...            0.00000            0.155778  0.015681   73   
3        0    0  ...            0.01337            0.085037  0.007606   53   
4        0    0  ...            0.00000            0.058852  0.041542   50   
...    ...  ...  ...                ...                 ...       ...  ...   
27858    0    0  ...            0.00000            0.229426  0.007551   50   
27859    0    0  ...            0.00000            0.066667  0.011185   60   
27860    0    0  ...            0.00000            0.132981  0.015684   60   
27861    0    0  ...            0.00000            0.277037  0.008397   56   
27862    0    0  ...            0.00000            0.140685  0.006038   60   

      dist_scaled  inv_deg_scaled  inv_velo_scaled   CCATmed  invVELOmed   
0        0.125762        0.544900         0.147660  0.301249    0.062690  \
1        0.145049        0.949755         0.231605  0.244543    0.113152   
2        0.193456        0.259163         0.196273  0.234858    0.189912   
3        0.129802        0.868918         0.087964  0.389112    0.069009   
4        0.936662        1.000000         0.107182  0.234858    0.189912   
...           ...             ...              ...       ...         ...   
27858    0.201416        1.000000         0.044559  0.338043    0.043109   
27859    0.064243        0.608108         0.199451  0.234858    0.189912   
27860    0.083408        0.572917         0.134337  0.244543    0.113152   
27861    0.427906        0.748069         0.036863  0.301249    0.062690   
27862    0.152231        0.608108         0.074930  0.301249    0.062690   

             VR  
0      0.271912  
1      0.221730  
2      0.215046  
3      0.351097  
4      0.229160  
...         ...  
27858  0.305107  
27859  0.212592  
27860  0.221032  
27861  0.273807  
27862  0.272078  

[1511 rows x 21 columns]

In [14]:
landscape_dict["WtFib"]

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR  mac   
6633    0.028569    0.002332    0.211259        80.530242  0  0  0     0    0  \
6634    0.002677   -0.007119    0.301441       276.028593  0  0  0     0    0   
6635   -0.006586    0.001626    0.339790       282.541646  0  0  0     0    0   
6636   -0.004062    0.011612    0.313816       191.022168  0  0  0     0    0   
6637   -0.020976    0.000697    0.395898       193.642173  0  0  0     0    0   
...          ...         ...         ...              ... .. .. ..   ...  ...   
7767    0.035519    0.005709    0.295729       244.941703  0  0  0     0    0   
7768    0.013063   -0.013518    0.319500       263.922364  0  0  0     0    0   
7769    0.003459    0.021346    0.279131        91.355214  0  0  0     0    0   
7770    0.027127   -0.001343    0.259780       207.349972  0  0  0     0    0   
7771   -0.001538   -0.005911    0.350759       282.467727  0  0  0     0    0   

      fib  ... OWNsig_stemO_UCell  OWNsig_stemS_UCell      dist  deg   
6633    1  ...           0.006074            0.230463  0.009271   70  \
6634    1  ...           0.000000            0.506056  0.006843   55   
6635    1  ...           0.013667            0.463593  0.006825   54   
6636    1  ...           0.000000            0.562259  0.007560   57   
6637    1  ...           0.397778            0.383222  0.007949   57   
...   ...  ...                ...                 ...       ...  ...   
7767    1  ...           0.000000            0.127630  0.031458   50   
7768    1  ...           0.000000            0.281185  0.007886   71   
7769    1  ...           0.000000            0.242185  0.009613   51   
7770    1  ...           0.000000            0.382167  0.009231   58   
7771    1  ...           0.000000            0.609185  0.004902   54   

     dist_scaled  inv_deg_scaled  inv_velo_scaled   CCATmed  invVELOmed   
6633    0.009226        0.328185         0.637838  0.247272    0.151823  \
6634    0.246332        0.786241         0.026197  0.324148    0.037607   
6635    0.209827        0.806452         0.020389  0.312962    0.096427   
6636    0.285858        0.679117         0.138316  0.312962    0.096427   
6637    0.148760        0.715605         0.133390  0.383408    0.120595   
...          ...             ...              ...       ...         ...   
7767    0.780503        1.000000         0.058173  0.292534    0.043742   
7768    0.040550        0.304530         0.037754  0.292534    0.043742   
7769    0.270472        0.948767         0.535508  0.285356    0.429171   
7770    0.008065        0.675676         0.109648  0.247272    0.151823   
7771    0.019354        0.825826         0.020454  0.324148    0.037607   

            VR  
6633  0.222684  
6634  0.292659  
6635  0.283689  
6636  0.284422  
6637  0.346861  
...        ...  
7767  0.266695  
7768  0.263458  
7769  0.268428  
7770  0.222667  
7771  0.291806  

[1139 rows x 21 columns]

In [15]:
landscape_dict["AK"]

phateepi_1  phateepi_2  SCENT_ccat  velocity_length  A  K  P  WENR  mac   
2480    0.003240    0.016035    0.412615       103.453230  1  1  0     0    0  \
2481   -0.016968   -0.007710    0.391436        77.548857  1  1  0     0    0   
2482    0.006557    0.004918    0.363780       110.565845  1  1  0     0    0   
2483   -0.006996   -0.007648    0.335951        78.394814  1  1  0     0    0   
2484   -0.028062    0.014227    0.399498        60.276537  1  1  0     0    0   
...          ...         ...         ...              ... .. .. ..   ...  ...   
4335   -0.008400   -0.004858    0.401780        70.411602  1  1  0     0    0   
4336    0.009121   -0.014316    0.359641        86.534077  1  1  0     0    0   
4337   -0.017137   -0.003249    0.408179       114.401401  1  1  0     0    0   
4338   -0.010983   -0.004122    0.423684       100.011907  1  1  0     0    0   
4339   -0.025789    0.007222    0.425584        75.027410  1  1  0     0    0   

      fib  ... OWNsig_stemO_UCell  OWNsig_stemS_UCell      dist  deg   
2480    0  ...           0.307222            0.167796  0.006067   65  \
2481    0  ...           0.312296            0.092093  0.015171   65   
2482    0  ...           0.329222            0.146759  0.009984   57   
2483    0  ...           0.020519            0.058222  0.005786   59   
2484    0  ...           0.385741            0.124241  0.009885   68   
...   ...  ...                ...                 ...       ...  ...   
4335    0  ...           0.411444            0.089111  0.006204   60   
4336    0  ...           0.038741            0.084074  0.008323   56   
4337    0  ...           0.284037            0.105444  0.011822   64   
4338    0  ...           0.575481            0.089889  0.005247   68   
4339    0  ...           0.369815            0.180352  0.005551   50   

     dist_scaled  inv_deg_scaled  inv_velo_scaled   CCATmed  invVELOmed   
2480    0.016260        0.397022         0.446485  0.362479    0.274071  \
2481    0.548308        0.465587         0.671038  0.415419    0.580216   
2482    0.297065        0.679117         0.403241  0.362479    0.274071   
2483    0.122754        0.641319         0.661361  0.383532    0.421313   
2484    0.255870        0.386997         0.928015  0.415419    0.580216   
...          ...             ...              ...       ...         ...   
4335    0.171561        0.608108         0.761941  0.383532    0.421313   
4336    0.054286        0.748069         0.577921  0.355903    0.334453   
4337    0.363017        0.493421         0.382152  0.415419    0.580216   
4338    0.050685        0.434492         0.469616  0.393207    0.407782   
4339    0.016127        1.000000         0.701177  0.415419    0.580216   

            VR  
2480  0.326677  
2481  0.405690  
2482  0.334373  
2483  0.350351  
2484  0.388723  
...        ...  
4335  0.352407  
4336  0.322129  
4337  0.394940  
4338  0.355953  
4339  0.374812  

[1860 rows x 21 columns]

In [16]:
df_landscape = pd.concat([landscape_dict["WT"], landscape_dict["WtFib"], landscape_dict["WENR"], landscape_dict["AK"]], keys=landscape_dict.keys())
df_landscape = df_landscape[["phateepi_1","phateepi_2","curatedCLUST","VR",
    "CCATmed","invVELOmed",
    "dist_scaled"]]
df_landscape

phateepi_1  phateepi_2      curatedCLUST        VR   CCATmed   
WT 0      -0.003110   -0.003080              TA 1  0.271912  0.301249  \
   1       0.024983    0.029213      Goblet / DCS  0.221730  0.244543   
   2       0.037142    0.007396   Late Enterocyte  0.215046  0.234858   
   3      -0.021990    0.000884            proCSC  0.351097  0.389112   
   4       0.041909    0.035762   Late Enterocyte  0.229160  0.234858   
...             ...         ...               ...       ...       ...   
AK 4335   -0.008400   -0.004858              TA 1  0.352407  0.383532   
   4336    0.009121   -0.014316  Early Enterocyte  0.322129  0.355903   
   4337   -0.017137   -0.003249            proCSC  0.394940  0.415419   
   4338   -0.010983   -0.004122              TA 2  0.355953  0.393207   
   4339   -0.025789    0.007222            proCSC  0.374812  0.415419   

         invVELOmed  dist_scaled  
WT 0       0.062690     0.125762  
   1       0.113152     0.145049  
   2       0.189912     0.193456  
   3       0.069009     0.129802  
   4       0.189912     0.936662  
...             ...          ...  
AK 4335    0.421313     0.171561  
   4336    0.334453     0.054286  
   4337    0.580216     0.363017  
   4338    0.407782     0.050685  
   4339    0.580216     0.016127  

[5901 rows x 7 columns]

In [17]:
#Save data to file:
df_landscape.reset_index().drop(["level_1"], axis=1).to_csv("output/dLANDSCAPE_data.csv", index=False)